# Visualization

author: Jasmine Qin  
date: 2020-06-02

In [ ]:
import pandas as pd
import geopandas as gpd
import numpy as np
import json

import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import iplot

import dash
import dash_core_components as dcc
import dash_html_components as html

In [ ]:
licence_train = pd.read_csv("../../data/processed/train_licence_vis.csv")
licence_validate = pd.read_csv("../../data/processed/validate_licence_vis.csv")
parking = pd.read_csv("../../data/processed/paking_meter_vis.csv")
disability_parking = pd.read_csv("../../data/processed/disability_parking_vis.csv")
boundary_df = gpd.read_file("../../data/raw/local_area_boundary.geojson")

with open("../../data/raw/local_area_boundary.geojson") as f:
    boundary = json.load(f)
    
for i in boundary['features']:
    i['id'] = i['properties']['mapid']

px.set_mapbox_access_token(open(".mapbox_token").read())
mapbox_access_token = open(".mapbox_token").read()

In [ ]:
#licence_train.head(3)

## Plotly Express

In [89]:
# using plotly express
boundary_df['color'] = np.random.randint(7, 50, size=22)
licence_validate = licence_validate[licence_validate.BusinessIndustry.notnull()]
licence_validate['FOLDERYEAR'] = [int(i) for i in licence_validate['FOLDERYEAR']]
licence_validate = licence_validate.sort_values('FOLDERYEAR')

industries = licence_validate.BusinessIndustry.unique()

scatter = px.scatter_mapbox(licence_validate, 
                            lat="coord-y", 
                            lon="coord-x", 
                            size_max=15,
                            hover_name="BusinessName",
                            animation_frame="FOLDERYEAR",
                            color="BusinessIndustry")

choro = px.choropleth_mapbox(boundary_df,
                             locations="mapid",
                             geojson=boundary,
                             opacity=0.1,
                             color="color",
                             color_continuous_scale="Viridis"
                             )

scatter.update_layout(height=800,
                      width=1000,
                      coloraxis_showscale=False, 
                      legend_orientation="h",
                      mapbox_zoom=11,
                      legend=dict(x=0, y=1.2),
                      mapbox_style='dark',
                   mapbox_center={"lat": 49.250, "lon": -123.121})

scatter.add_trace(choro.data[0])


In [ ]:
# convert to dash object
app = dash.Dash()
app.layout = html.Div([
    dcc.Graph(figure=scatter)
])
app.run_server(debug=True)

## Plotly Graphic Object

In [ ]:
# using plotly go
choro = go.Figure(go.Choroplethmapbox(geojson=boundary, locations=boundary_df.mapid, z=boundary_df.color,
                                      colorscale="Viridis",
                                      marker_opacity=0.5, marker_line_width=0))

scatter = go.Figure(go.Scattermapbox(lat=licence_validate['coord-y'],
                         lon=licence_validate['coord-x']))

layout = go.Layout(width=900, height=700,
                   mapbox=dict(center={"lat": 49.248, "lon": -123.169},            
                                 accesstoken=mapbox_access_token,
                                 zoom=10,
                                 style="dark"))


fig=go.Figure(data=[choro.data[0], scatter.data[0]], layout=layout)
iplot(fig)

## Animation

In [ ]:
# data
years = sorted(list(licence_validate.FOLDERYEAR.unique()))
viz_data = []

for year in years:
    year_data_scatt = dict(
        lat = licence_validate.loc[licence_validate['FOLDERYEAR'] == year, 'coord-y'],
        lon = licence_validate.loc[licence_validate['FOLDERYEAR'] == year, 'coord-x'],
        marker = dict(size = 4, 
                      opacity = 0.5),
        name = int(year),
        type = 'scattermapbox'
    )
    
    year_data_choro = dict(
        geojson = boundary,
        locations = boundary_df.mapid,
        z = np.random.randint(7, 50, size=22),
        colorscale = "Viridis",
        marker_opacity = 0.3, 
        name = int(year),
        marker_line_width = 1,
        type = 'choroplethmapbox'
    )
    
    
    viz_data.append(year_data_scatt)

In [ ]:
# layout
layout = dict(
    height=800,
    width=1000,
    showlegend = False,
    mapbox=dict(center={"lat": 49.248, "lon": -123.169},            
                                 accesstoken=mapbox_access_token,
                                 zoom=10,
                                 style="dark")
)

In [ ]:
# slider
steps = []

for i in range(len(viz_data)):
    step = dict(method='restyle',
                args=['visible', [False] * len(viz_data)],
                label='Year {}'.format(i+1997)) 
    step['args'][1][i] = True
    steps.append(step)


sliders = [dict(active=1, 
                pad={"t": 1},
                steps=steps,
                transition={
                    "duration": 300, 
                    "easing": "cubic-in-out"}
               )]

layout['sliders'] = sliders

In [ ]:
fig = dict(data=viz_data, layout=layout)
iplot(fig)

## Colors

In [ ]:
years = sorted(list(licence_validate.FOLDERYEAR.unique()))
industries = list(licence_validate.BusinessIndustry.unique())
viz_data = []

colors = ['rgb(239,243,255)','rgb(189,215,231)','rgb(107,174,214)','rgb(33,113,181)',
          'rgb(245,33,55)','rgb(189,222,231)','rgb(567,174,214)','rgb(33,113,181)',
          'rgb(239,243,255)','rgb(189,215,231)','rgb(107,255,214)','rgb(45,113,181)',
          'rgb(239,243,255)','rgb(189,255,231)','rgb(107,54,214)','rgb(33,113,180)']

for y in years:
    
    fig = go.Figure()
    
    for i in range(len(industries)):
        data_industry = licence_validate.loc[licence_validate.BusinessIndustry == industries[i]]
        
        fig.add_trace(go.Scattermapbox(
            lat = data_industry['coord-y'],
            lon = data_industry['coord-x'],
            name = i,
            text = i,
            marker = dict(color = colors[i],
                          size = 4, 
                          opacity = 0.5
                          )
        ))
    
    viz_data.append(fig)